In [ ]:
!pip3 install bibtexparser polars datasets -q

In [2]:
!wget https://aclanthology.org/anthology+abstracts.bib.gz

--2025-05-16 16:05:50--  https://aclanthology.org/anthology+abstracts.bib.gz
Resolving aclanthology.org (aclanthology.org)... 157.245.140.42
Connecting to aclanthology.org (aclanthology.org)|157.245.140.42|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 31139200 (30M) [application/x-gzip]
Saving to: ‘anthology+abstracts.bib.gz’

anthology+abstracts 100%[===================>]  29.70M   134MB/s    in 0.2s    

2025-05-16 16:05:50 (134 MB/s) - ‘anthology+abstracts.bib.gz’ saved [31139200/31139200]



In [3]:
!gunzip anthology+abstracts.bib.gz

In [4]:
import bibtexparser
import json

def bib_to_json(bib_file_path, json_file_path=None):
    # Read the BIB file
    with open(bib_file_path, 'r', encoding='utf-8') as bibtex_file:
        bib_database = bibtexparser.load(bibtex_file)

    # Convert to JSON
    json_data = json.dumps(bib_database.entries, indent=4, ensure_ascii=False)

    # Write to file if path is provided
    if json_file_path:
        with open(json_file_path, 'w', encoding='utf-8') as json_file:
            json_file.write(json_data)
        print(f"Converted BIB to JSON and saved to {json_file_path}")

    return json_data

In [5]:
result = bib_to_json("anthology+abstracts.bib", "acl_abstracts.json")
print("First few characters of the JSON:", result[:1000])

Converted BIB to JSON and saved to acl_abstracts.json
First few characters of the JSON: [
    {
        "url": "https://aclanthology.org/2025.wraicogs-1.0/",
        "publisher": "International Committee on Computational Linguistics",
        "address": "Abu Dhabi, UAE",
        "year": "2025",
        "month": "January",
        "editor": "Zock, Michael  and\nInui, Kentaro  and\nYuan, Zheng",
        "title": "Proceedings of the First Workshop on Writing Aids at the Crossroads of AI, Cognitive Science and NLP (WRAICOGS 2025)",
        "ENTRYTYPE": "proceedings",
        "ID": "wraicogs-ws-2025-1"
    },
    {
        "abstract": "Large Language Models (LLMs) have been used to generate texts in response to different writing tasks: reports, essays, story telling. However, language models do not have a metarepresentation of the text writing process, nor inherent communication learning needs, comparable to those of young human students. This paper introduces a fine-grained linguistic and 

# Convert to a dataframe

In [ ]:
import polars as pl
pl.Config.set_fmt_str_lengths(100)

In [10]:
df = pl.read_json("acl_abstracts.json",
                  schema={
                      "ENTRYTYPE": pl.Utf8,
                      "ID": pl.Utf8,
                      "year": pl.Utf8,
                      "title": pl.Utf8,
                      "abstract": pl.Utf8,
                  }
                  )

In [11]:
df = df.filter(pl.col("ENTRYTYPE") == "inproceedings").drop("ENTRYTYPE")
df = df.drop_nulls()
df = df.with_columns([
        pl.col("title").str.replace_all(r"\{|\}", ""),
        pl.col("year").cast(pl.Int64)
        ])

print(df.shape[0])
df.head()

60497


shape: (5, 4)
┌──────────────────────────────┬──────┬──────────────────────────────┬─────────────────────────────┐
│ ID                           ┆ year ┆ title                        ┆ abstract                    │
│ ---                          ┆ ---  ┆ ---                          ┆ ---                         │
│ str                          ┆ i64  ┆ str                          ┆ str                         │
╞══════════════════════════════╪══════╪══════════════════════════════╪═════════════════════════════╡
│ buhnila-etal-2025-chain      ┆ 2025 ┆ Chain-of-MetaWriting:        ┆ Large Language Models       │
│                              ┆      ┆ Linguistic and Textual       ┆ (LLMs) have been used to    │
│                              ┆      ┆ Analysis of How Small        ┆ generate texts in response  │
│                              ┆      ┆ Language Models Write Young  ┆ to different writing tasks… │
│                              ┆      ┆ Stude…                       ┆                             │
│ shi-penn-2025-semantic       ┆ 2025 ┆ Semantic Masking in a        ┆ In this paper, we introduce │
│                              ┆      ┆ Needle-in-a-haystack Test    ┆ the concept of Semantic     │
│                              ┆      ┆ for Evaluating Large         ┆ Masking, where semantically │
│                              ┆      ┆ Language Model Long-Text     ┆ coherent surrounding…       │
│                              ┆      ┆ Capabi…                      ┆                             │
│ khallaf-etal-2025-reading    ┆ 2025 ┆ Reading Between the Lines: A ┆ Our research aims at better │
│                              ┆      ┆ dataset and a study on why   ┆ understanding what makes a  │
│                              ┆      ┆ some texts are tougher than  ┆ text difficult to read for  │
│                              ┆      ┆ others                       ┆ specific audiences…         │
│ jourdan-etal-2025-pararev    ┆ 2025 ┆ ParaRev : Building a dataset ┆ Revision is a crucial step  │
│                              ┆      ┆ for Scientific Paragraph     ┆ in scientific writing,      │
│                              ┆      ┆ Revision annotated with      ┆ where authors refine their  │
│                              ┆      ┆ revision instruction         ┆ work to improve clarity…    │
│ maggi-vitaletti-2025-towards ┆ 2025 ┆ Towards an operative         ┆ Nowadays, AI is present in  │
│                              ┆      ┆ definition of creative       ┆ all our activities. This    │
│                              ┆      ┆ writing: a preliminary       ┆ pervasive presence is       │
│                              ┆      ┆ assessment of creativeness   ┆ perceived as a threat by m… │
│                              ┆      ┆ in AI …                      ┆                             │
└──────────────────────────────┴──────┴──────────────────────────────┴─────────────────────────────┘

In [12]:
df[18]["abstract"].item()

'Named Entity Recognition (NER), a fundamental task in Natural Language Processing (NLP), has shown significant advancements for high-resource languages. However, due to a lack of annotated datasets and limited representation in Pre-trained Language Models (PLMs), it remains understudied and challenging for low-resource languages. To address these challenges, in this paper, we propose a data augmentation technique that generates culturally plausible sentences and experiments on four low-resource Pakistani languages; Urdu, Shahmukhi, Sindhi, and Pashto. By fine-tuning multilingual masked Large Language Models (LLMs), our approach demonstrates significant improvements in NER performance for Shahmukhi and Pashto. We further explore the capability of generative LLMs for NER and data augmentation using few-shot learning.'

In [13]:
df.tail(1)["abstract"].item()

'We used to think that the output of a translation machine would be stylistically inelegant, but this would be tolerable if only the message got across. We now find that getting the message across accurately is difficult, but we may be able to have stylistic elegance in the output since much of style reflects depth phenomena and thus is systematic. As an example, the order of the clauses in many twoclause sentences can be reversed without a change of meaning, but the same is not normally true of sentences with more than two clauses. The meaning usually changes when the clause order is changed. Equivalently, there appear to be severe restrictions on clause order for any given meaning. These restrictions appear to follow from depth considerations. The idea is being investigated that there is a normal depth-related clause order and any deviations from this order must be signalled by special syntactic or semantic devices. The nature of these devices is being explored. When translating mult

In [14]:
min(df["year"].to_list())

1963

# Push to the hb

In [16]:
from datasets import Dataset

dataset = Dataset.from_polars(df)
dataset

Dataset({
    features: ['ID', 'year', 'title', 'abstract'],
    num_rows: 60497
})

In [ ]:
dataset.push_to_hub("acl-abstracts")